In [3]:
import csv_to_sqlite
from plotly.subplots import make_subplots
import matplotlib.pyplot as plt
import os
import sqlite3
import pandas as pd
import plotly.express as px
import sqlite3
import plotly.graph_objs as go
import plotly.offline as pyo


def fix_cols(df):
    """remove uppercases and periods from col names"""
    new_cols = []

    cols = df.columns

    for col in cols:
        col = col.lower().replace('.', '_')
        col = col.replace(' ', '_')
        new_cols.append(col)

    df.columns = new_cols

    return df

In [2]:
conv_list = os.listdir('./data/csv')
conv_list = [os.path.join('data\\csv', path) for path in conv_list if path.endswith('csv')]
print(conv_list)

['data\\csv\\gfb.csv', 'data\\csv\\iats.csv', 'data\\csv\\iats2.csv', 'data\\csv\\long_term.csv', 'data\\csv\\tc_disp.csv']


In [18]:
# print(fix_cols(pd.read_csv('data/long_term.csv')))

for f in conv_list:
    df = fix_cols(pd.read_csv(f))
    df.to_csv(f)
    print(df.columns)

Index(['frame', 'time_ms', 'time_us', 'rpm', 'vss', 'gear', 'ptank', 'map',
       'bp', 'bp_cmd', 'tpedal', 'tplate', 'afm_v', 'afm_hz', 'afm', 'afm_c',
       'airc', 'egr', 'iat', 'iat2', 'ect', 'ect2', 'pa', 'oil_press',
       'cvt_temp', 'inj', 'inj_bank_2', 'duty', 'difp', 'difpcmd', 'fuelp',
       'ign', 'cam', 'camcmd', 'excam', 'excamcmd', 'wg', 'wgcmd', 'vts',
       'svs', 'purge', 'accl', 'bc_duty', 'af', 'af_bank_2', 'af_corr',
       'wide_v', 'wide', 'afcmd', 'afcmd_bank_2', 's_trim', 'l_trim',
       's_trim_bank_2', 'l_trim_bank_2', 'trim', 'fuel_status',
       'fuel_status_bank_2', 'ethanol', 'k_level', 'k_retard', 'k_retard_1',
       'k_retard_2', 'k_retard_3', 'k_retard_4', 'k_control', 'ign_limit',
       'k_count', 'k_count_1', 'k_count_2', 'k_count_3', 'k_count_4',
       'k_count_5', 'k_count_6', 'bat', 'cat_t', 'abs_lf', 'abs_rf', 'abs_lr',
       'abs_rr', 'clutch_pos', 'brake_press', 'steer_ang', 'steer_trq',
       'g_lat', 'g_long', 'g_z', 'yaw', 'eco',

In [19]:
options = csv_to_sqlite.CsvOptions(encoding='utf-8')

csv_to_sqlite.write_csv(conv_list, 'fk8_data.sqlite', options)


Written 402604 rows into 4 tables in 10.818 seconds


402604

In [6]:
con = sqlite3.connect('./data/fk8_data.sqlite')


In [21]:
df = pd.read_sql(
    'SELECT '
    'time_ms'
    ', g_lat'
    ', g_long'
    ', steer_ang'
    ' FROM gfb'
    , con=con)

In [23]:
df['comb'] = df[['g_lat', 'g_long']].apply(lambda x: ', '.join(x.astype(str)), axis=1)

fig = px.scatter(
    df,
    x='g_lat',
    y='g_long',
    animation_frame='time_ms',
    text=df['comb']
)

pyo.plot(fig)



'temp-plot.html'

In [16]:
update_men = [
    {
        'active': 1,
        "buttons": [
            {
                "args": [None, {
                    "frame": {"duration": 50, "redraw": False}, 'mode': 'immediate',
                    "fromcurrent": True, "transition": {"duration": 50}
                }
                         ],
                "label": None,
                "method": "animate"
            },
            {
                "args": [[None], {
                    "frame": {"duration": None, "redraw": False},
                    "mode": "immediate",
                    "transition": {"duration": 0}
                }
                         ],
                "label": None,
                "method": "animate"
            }
        ]
    }]

layout = go.Layout(updatemenus=update_men, xaxis={'range': [-0.5, 1.5]}, yaxis={'range': [-0.5, 1.5]})

fig.update_layout(layout)

fig.update_traces(marker=dict(size=20), textposition='top center', textfont_size=20)


In [10]:
pyo.plot(fig)

'temp-plot.html'

In [24]:
df = pd.read_sql(
    'SELECT *'
    ' FROM long_term'
    ' WHERE frame BETWEEN 100000 AND 110000',
    con
)

In [ ]:
df['ms_corr'] = df['time_ms'] - 789410
df['s_corr'] = df['ms_corr'] / 1000
df['s_corr']
fig = make_subplots(rows=2, cols=2, shared_xaxes=True)

fig.add_trace(
    go.Scatter(x=df['s_corr'], y=df['wg'], name='Wastegate'),
    row=1, col=1
)

fig.add_trace(
    go.Scatter(x=df['s_corr'], y=df['wgcmd'], name='Wastegate Command'),
    row=1, col=1
)

fig.add_trace(
    go.Scatter(x=df['s_corr'], y=df['map'], name='MAP'),
    row=1, col=2
)

fig.add_trace(
    go.Scatter(x=df['s_corr'], y=df['bp_cmd'], name='MAP Command'),
    row=1, col=2
)

fig.add_trace(
    go.Scatter(x=df['s_corr'], y=df['bp'], name='Boost Pressure'),
    row=1, col=2
)

fig.add_trace(
    go.Scatter(x=df['s_corr'], y=df['af'], name='A/F Ratio'),
    row=2, col=1
)

fig.add_trace(
    go.Scatter(x=df['s_corr'], y=df['afcmd'], name='A/F Ratio Command'),
    row=2, col=1
)

fig.add_trace(
    go.Scatter(x=df['s_corr'], y=df['s_trim'], name='S.Trim'),
    row=2, col=1
)

fig.add_trace(
    go.Scatter(x=df['s_corr'], y=df['cam'], name='Cam Angle'),
    row=2, col=2
)

fig.add_trace(
    go.Scatter(x=df['s_corr'], y=df['camcmd'], name='Cam Angle Command'),
    row=2, col=2
)

fig.update_layout(
    xaxis=dict(
        autorange=True, rangeslider=dict(autorange=True, thickness=0.05)
    ),
    xaxis2=dict(
        autorange=True, rangeslider=dict(autorange=True, thickness=0.05)
    )
)

In [ ]:
df = pd.read_sql('SELECT * FROM gfb', con)

g = px.line(df, x='frame', y=['tpedal', 'steer_ang'])

tc = [[1569, 1617],
      [1640, 1659],
      [1667, 1673],
      [1625, 1639],
      [1814, 1820],
      [2059, 2065],
      [2101, 2121],
      [2136, 2156],
      [2185, 2191],
      [2206, 2219],
      [2269, 2296],
      [2367, 2436],
      [2542, 2555],
      [2570, 2590],
      [2598, 2611],
      [2626, 2632],
      [2675, 2695]]

In [ ]:
for x in range(len(tc)):
    g.add_vrect(x0=tc[x][0], x1=tc[x][1],
                fillcolor='black', opacity=0.15, line_width=0, visible=True)

g.update_layout(
    xaxis=dict(
        range=[0,3200], rangeslider=dict(autorange=True)
    ),
    showlegend=True,
title='Activity of traction control as steering angle and throttle position vary'
)



def add_tc():
    for x in range(len(tc)):
        g.add_vrect(
            x0=tc[x][0],
            x1=tc[x][1],
            fillcolor='black',
            opacity=0.15,
            line_width=0
        )


In [ ]:
for i in range(len(tc)):
    g.add_vrect(tc[i][0], tc[i][1], visible=False)